In [1]:
import os
from dotenv import load_dotenv

load_dotenv()

os.environ['REPLICATE_API_TOKEN'] = os.getenv('REPLICATE_API_TOKEN')
model_path = "ibm-granite/granite-4.0-h-small"
from langchain_community.llms import Replicate

model = Replicate(
    model=model_path,
    model_kwargs={
        "max_tokens": 2000,
        "min_tokens": 200,
        "presence_penalty": 0,
        "frequency_penalty": 0,
    },
)


/home/ubuntu/miniconda3/envs/langgraph-dev/lib/python3.12/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
import itertools
from typing import Iterator, Callable

from docling.document_converter import DocumentConverter
from docling_core.transforms.chunker.hierarchical_chunker import HierarchicalChunker
from docling_core.transforms.chunker.base import BaseChunk

def chunk_document(source: str, *, dropwhile: Callable[[BaseChunk], bool] = lambda c: False, takewhile: Callable[[BaseChunk], bool] = lambda c: True) -> Iterator[BaseChunk]:
    """Read the document and perform a hierarchical chunking"""
    converter = DocumentConverter()
    chunks = HierarchicalChunker().chunk(converter.convert(source=source).document)
    return itertools.takewhile(takewhile, itertools.dropwhile(dropwhile, chunks))

def chunk_dropwhile(chunk: BaseChunk) -> bool:
    """Ignore front matter prior to the book start"""
    return "WALDEN" not in chunk.meta.headings

def chunk_takewhile(chunk: BaseChunk) -> bool:
    """Ignore remaining chunks once we see this heading"""
    return "ON THE DUTY OF CIVIL DISOBEDIENCE" not in chunk.meta.headings

chunks = chunk_document(
    "https://www.gutenberg.org/cache/epub/205/pg205-images.html",
    dropwhile=chunk_dropwhile,
    takewhile=chunk_takewhile,
)
for chunk in chunks:
    print(chunk)


2025-10-11 19:12:42,499 - INFO - detected formats: [<InputFormat.HTML: 'html'>]
2025-10-11 19:12:42,542 - INFO - Going to convert document batch...
2025-10-11 19:12:42,543 - INFO - Initializing pipeline for SimplePipeline with options hash 995a146ad601044538e6a923bea22f4e
2025-10-11 19:12:42,564 - INFO - Loading plugin 'docling_defaults'
2025-10-11 19:12:42,569 - INFO - Registered picture descriptions: ['vlm', 'api']
2025-10-11 19:12:42,569 - INFO - Processing document pg205-images.html
2025-10-11 19:12:42,578 - INFO - deleted item in tree at stack: (2, 2, 1) => #/texts/26
2025-10-11 19:12:42,579 - INFO - deleted item in tree at stack: (2, 2, 1) => #/texts/26
2025-10-11 19:12:42,580 - INFO - deleted item in tree at stack: (2, 2, 1) => #/texts/26
2025-10-11 19:12:42,582 - INFO - deleted item in tree at stack: (2, 2, 1) => #/texts/26
2025-10-11 19:12:42,583 - INFO - deleted item in tree at stack: (2, 2, 1) => #/texts/26
2025-10-11 19:12:42,583 - INFO - deleted item in tree at stack: (2, 

text='When I wrote the following pages, or rather the bulk of them, I lived alone, in' meta=DocMeta(schema_name='docling_core.transforms.chunker.DocMeta', version='1.0.0', doc_items=[TextItem(self_ref='#/texts/28', parent=RefItem(cref='#/texts/27'), children=[], content_layer=<ContentLayer.BODY: 'body'>, label=<DocItemLabel.TEXT: 'text'>, prov=[], orig='When I wrote the following pages, or rather the bulk of them, I lived alone, in', text='When I wrote the following pages, or rather the bulk of them, I lived alone, in', formatting=None, hyperlink=None)], headings=['WALDEN', 'Economy'], captions=None, origin=DocumentOrigin(mimetype='text/html', binary_hash=11066415575754135830, filename='pg205-images.html', uri=None))
text='the woods, a mile from any neighbor, in a house which I had built myself, on' meta=DocMeta(schema_name='docling_core.transforms.chunker.DocMeta', version='1.0.0', doc_items=[TextItem(self_ref='#/texts/29', parent=RefItem(cref='#/texts/27'), children=[], content_layer

In [3]:
def merge_chunks(chunks: Iterator[BaseChunk], *, headings: Callable[[BaseChunk], list[str]] = lambda c: c.meta.headings) -> Iterator[dict[str, str]]:
    """Merge chunks having the same headings"""
    prior_headings: list[str] | None = None
    document: dict[str, str] = {}
    doc_id = 0
    for chunk in chunks:
        text = chunk.text.replace('\r\n', '\n')
        current_headings = headings(chunk)
        if prior_headings != current_headings:
            if document:
                yield document
            prior_headings = current_headings
            document = {
                'doc_id': str(doc_id:=doc_id+1),
                'title': " - ".join(current_headings),
                'text': text
            }
        else:
            document['text'] += f"\n\n{text}"
    if document:
        yield document

def chunk_headings(chunk: BaseChunk) -> list[str]:
    """Use the h1 and h2 (chapter) headings"""
    return chunk.meta.headings[:2]

documents: list[dict[str, str]] = list(merge_chunks(
    chunk_document(
        "https://www.gutenberg.org/cache/epub/205/pg205-images.html",
        dropwhile=chunk_dropwhile,
        takewhile=chunk_takewhile,
    ),
    headings=chunk_headings,
))
documents


2025-10-11 19:12:43,958 - INFO - detected formats: [<InputFormat.HTML: 'html'>]
2025-10-11 19:12:43,985 - INFO - Going to convert document batch...
2025-10-11 19:12:43,985 - INFO - Initializing pipeline for SimplePipeline with options hash 995a146ad601044538e6a923bea22f4e
2025-10-11 19:12:43,986 - INFO - Processing document pg205-images.html
2025-10-11 19:12:43,991 - INFO - deleted item in tree at stack: (2, 2, 1) => #/texts/26
2025-10-11 19:12:43,992 - INFO - deleted item in tree at stack: (2, 2, 1) => #/texts/26
2025-10-11 19:12:43,993 - INFO - deleted item in tree at stack: (2, 2, 1) => #/texts/26
2025-10-11 19:12:43,994 - INFO - deleted item in tree at stack: (2, 2, 1) => #/texts/26
2025-10-11 19:12:43,995 - INFO - deleted item in tree at stack: (2, 2, 1) => #/texts/26
2025-10-11 19:12:43,996 - INFO - deleted item in tree at stack: (2, 2, 1) => #/texts/26
2025-10-11 19:12:43,997 - INFO - deleted item in tree at stack: (2, 2, 1) => #/texts/26
2025-10-11 19:12:43,997 - INFO - deleted

[{'doc_id': '1',
  'title': 'WALDEN - Economy',
  'text': 'When I wrote the following pages, or rather the bulk of them, I lived alone, in\n\nthe woods, a mile from any neighbor, in a house which I had built myself, on\n\nthe shore of Walden Pond, in Concord, Massachusetts, and earned my living by\n\nthe labor of my hands only. I lived there two years and two months. At present\n\nI am a sojourner in civilized life again.\n\nI should not obtrude my affairs so much on the notice of my readers if very\n\nparticular inquiries had not been made by my townsmen concerning my mode of\n\nlife, which some would call impertinent, though they do not appear to me at all\n\nimpertinent, but, considering the circumstances, very natural and pertinent.\n\nSome have asked what I got to eat; if I did not feel lonesome; if I was not\n\nafraid; and the like. Others have been curious to learn what portion of my\n\nincome I devoted to charitable purposes; and some, who have large families, how\n\nmany poor 

In [4]:
def generate(user_prompt: str, documents: list[dict[str, str]]) -> str:
    """Use manual prompt formatting"""
    docs_str = "\n\n".join([f"Title: {d['title']}\nText: {d['text']}" for d in documents])
    full_prompt = f"{user_prompt}\n\n{docs_str}"
    
    output = model.invoke(full_prompt)
    return output


In [5]:
user_prompt = """Using only the the book chapter document, compose a summary of the book chapter.

Your response should only include the summary. Do not provide any further explanation."""

summaries: list[dict[str, str]] = []

for i, document in enumerate(documents, start=1):
    print(f"============================= {document['title']} ({i}/{len(documents)}) =============================")
    output = generate(user_prompt, [document])
    summaries.append({
        'doc_id': document['doc_id'],
        'title': document['title'],
        'text': output,
    })

print("Summary count: " + str(len(summaries)))


============================= WALDEN - Economy (1/18) =============================


2025-10-11 19:12:45,293 - INFO - HTTP Request: GET https://api.replicate.com/v1/models/ibm-granite/granite-4.0-h-small "HTTP/1.1 200 OK"
2025-10-11 19:12:45,848 - INFO - HTTP Request: POST https://api.replicate.com/v1/models/ibm-granite/granite-4.0-h-small/predictions "HTTP/1.1 201 Created"
2025-10-11 19:12:46,532 - INFO - HTTP Request: GET https://api.replicate.com/v1/predictions/x7pey3tcnnrj40cstp68h5yj1r "HTTP/1.1 200 OK"
2025-10-11 19:12:47,199 - INFO - HTTP Request: GET https://api.replicate.com/v1/predictions/x7pey3tcnnrj40cstp68h5yj1r "HTTP/1.1 200 OK"
2025-10-11 19:12:47,881 - INFO - HTTP Request: GET https://api.replicate.com/v1/predictions/x7pey3tcnnrj40cstp68h5yj1r "HTTP/1.1 200 OK"
2025-10-11 19:12:48,536 - INFO - HTTP Request: GET https://api.replicate.com/v1/predictions/x7pey3tcnnrj40cstp68h5yj1r "HTTP/1.1 200 OK"
2025-10-11 19:12:49,246 - INFO - HTTP Request: GET https://api.replicate.com/v1/predictions/x7pey3tcnnrj40cstp68h5yj1r "HTTP/1.1 200 OK"
2025-10-11 19:12:49,915

============================= WALDEN - Where I Lived, and What I Lived For (2/18) =============================


2025-10-11 19:12:57,620 - INFO - HTTP Request: POST https://api.replicate.com/v1/models/ibm-granite/granite-4.0-h-small/predictions "HTTP/1.1 201 Created"
2025-10-11 19:12:58,265 - INFO - HTTP Request: GET https://api.replicate.com/v1/predictions/a88ng03tpsrj60cstp6am5bxh4 "HTTP/1.1 200 OK"
2025-10-11 19:12:58,917 - INFO - HTTP Request: GET https://api.replicate.com/v1/predictions/a88ng03tpsrj60cstp6am5bxh4 "HTTP/1.1 200 OK"
2025-10-11 19:12:59,568 - INFO - HTTP Request: GET https://api.replicate.com/v1/predictions/a88ng03tpsrj60cstp6am5bxh4 "HTTP/1.1 200 OK"
2025-10-11 19:13:00,259 - INFO - HTTP Request: GET https://api.replicate.com/v1/predictions/a88ng03tpsrj60cstp6am5bxh4 "HTTP/1.1 200 OK"
2025-10-11 19:13:00,949 - INFO - HTTP Request: GET https://api.replicate.com/v1/predictions/a88ng03tpsrj60cstp6am5bxh4 "HTTP/1.1 200 OK"
2025-10-11 19:13:01,631 - INFO - HTTP Request: GET https://api.replicate.com/v1/predictions/a88ng03tpsrj60cstp6am5bxh4 "HTTP/1.1 200 OK"
2025-10-11 19:13:02,275

============================= WALDEN - Reading (3/18) =============================


...

============================= WALDEN - Spring (17/18) =============================


2025-10-11 19:14:22,542 - INFO - HTTP Request: POST https://api.replicate.com/v1/models/ibm-granite/granite-4.0-h-small/predictions "HTTP/1.1 201 Created"
2025-10-11 19:14:23,209 - INFO - HTTP Request: GET https://api.replicate.com/v1/predictions/vsr1qyy6e9rj00cstp6r4y06qg "HTTP/1.1 200 OK"
2025-10-11 19:14:23,845 - INFO - HTTP Request: GET https://api.replicate.com/v1/predictions/vsr1qyy6e9rj00cstp6r4y06qg "HTTP/1.1 200 OK"
2025-10-11 19:14:24,526 - INFO - HTTP Request: GET https://api.replicate.com/v1/predictions/vsr1qyy6e9rj00cstp6r4y06qg "HTTP/1.1 200 OK"
2025-10-11 19:14:25,175 - INFO - HTTP Request: GET https://api.replicate.com/v1/predictions/vsr1qyy6e9rj00cstp6r4y06qg "HTTP/1.1 200 OK"
2025-10-11 19:14:25,816 - INFO - HTTP Request: GET https://api.replicate.com/v1/predictions/vsr1qyy6e9rj00cstp6r4y06qg "HTTP/1.1 200 OK"
2025-10-11 19:14:26,517 - INFO - HTTP Request: GET https://api.replicate.com/v1/predictions/vsr1qyy6e9rj00cstp6r4y06qg "HTTP/1.1 200 OK"
2025-10-11 19:14:27,212

============================= WALDEN - Conclusion (18/18) =============================


2025-10-11 19:14:32,963 - INFO - HTTP Request: POST https://api.replicate.com/v1/models/ibm-granite/granite-4.0-h-small/predictions "HTTP/1.1 201 Created"
2025-10-11 19:14:33,599 - INFO - HTTP Request: GET https://api.replicate.com/v1/predictions/k9z86qzf5nrj60cstp6v3zwme4 "HTTP/1.1 200 OK"
2025-10-11 19:14:34,277 - INFO - HTTP Request: GET https://api.replicate.com/v1/predictions/k9z86qzf5nrj60cstp6v3zwme4 "HTTP/1.1 200 OK"
2025-10-11 19:14:34,948 - INFO - HTTP Request: GET https://api.replicate.com/v1/predictions/k9z86qzf5nrj60cstp6v3zwme4 "HTTP/1.1 200 OK"
2025-10-11 19:14:35,585 - INFO - HTTP Request: GET https://api.replicate.com/v1/predictions/k9z86qzf5nrj60cstp6v3zwme4 "HTTP/1.1 200 OK"
2025-10-11 19:14:36,244 - INFO - HTTP Request: GET https://api.replicate.com/v1/predictions/k9z86qzf5nrj60cstp6v3zwme4 "HTTP/1.1 200 OK"
2025-10-11 19:14:36,929 - INFO - HTTP Request: GET https://api.replicate.com/v1/predictions/k9z86qzf5nrj60cstp6v3zwme4 "HTTP/1.1 200 OK"
2025-10-11 19:14:37,662

Summary count: 18


In [7]:
import textwrap

user_prompt = """Using only the book chapter summary documents, compose a single, unified summary of the book.

Your response should only include the unified summary. Do not provide any further explanation."""

output = generate(user_prompt, summaries)
print(textwrap.fill(output, width=80))


2025-10-11 19:15:36,933 - INFO - HTTP Request: POST https://api.replicate.com/v1/models/ibm-granite/granite-4.0-h-small/predictions "HTTP/1.1 201 Created"
2025-10-11 19:15:37,611 - INFO - HTTP Request: GET https://api.replicate.com/v1/predictions/sjfbpj7915rj00cstp7ajvcyp8 "HTTP/1.1 200 OK"
2025-10-11 19:15:38,283 - INFO - HTTP Request: GET https://api.replicate.com/v1/predictions/sjfbpj7915rj00cstp7ajvcyp8 "HTTP/1.1 200 OK"
2025-10-11 19:15:38,932 - INFO - HTTP Request: GET https://api.replicate.com/v1/predictions/sjfbpj7915rj00cstp7ajvcyp8 "HTTP/1.1 200 OK"
2025-10-11 19:15:39,611 - INFO - HTTP Request: GET https://api.replicate.com/v1/predictions/sjfbpj7915rj00cstp7ajvcyp8 "HTTP/1.1 200 OK"
2025-10-11 19:15:40,277 - INFO - HTTP Request: GET https://api.replicate.com/v1/predictions/sjfbpj7915rj00cstp7ajvcyp8 "HTTP/1.1 200 OK"
2025-10-11 19:15:40,899 - INFO - HTTP Request: GET https://api.replicate.com/v1/predictions/sjfbpj7915rj00cstp7ajvcyp8 "HTTP/1.1 200 OK"
2025-10-11 19:15:41,590

"Walden" by Henry David Thoreau is a reflection on the author's two-year
experiment of living simply and self-sufficiently in a small cabin near Walden
Pond in Concord, Massachusetts. Thoreau's main goal was to demonstrate that it
is possible to live a life of simplicity and self-reliance, free from the
distractions and demands of society. He discusses the cost of living, the value
of money, and the importance of living deliberately. Thoreau criticizes the
materialism and consumerism of his time, and argues that true wealth lies in the
richness of one's experiences and the depth of one's understanding, rather than
in the accumulation of possessions. He also emphasizes the importance of
solitude and spending time in nature, believing that by immersing oneself in the
natural world, one can gain a deeper understanding of oneself and the universe.
Throughout the book, Thoreau challenges readers to reconsider their priorities
and to live more deliberately and simply, with a focus on persona